# What we are going to do here is get model scores for Method of Victory models (mov)

In [1]:
import pandas as pd
import numpy as np
import random
import csv
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.tree import ExtraTreeClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.neighbors import RadiusNeighborsClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.linear_model import SGDClassifier
from sklearn.gaussian_process import GaussianProcessClassifier
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import BaggingClassifier
from sklearn.naive_bayes import BernoulliNB
from sklearn.calibration import CalibratedClassifierCV
from sklearn.svm import LinearSVC
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.linear_model import LogisticRegressionCV
from sklearn.discriminant_analysis import QuadraticDiscriminantAnalysis
#from sklearn.mixture import DPGMM

In [2]:
import sys
sys.path.append('../../automated_model_creation') #We need to access the function file

In [3]:
from functions import *


In [4]:
is_prod = False

if is_prod:
    model_file = '../../data/production_models_mov.csv'
else: #If not production then test
    model_file = '../../data/models_mov.csv'

In [5]:
#Load models
with open(model_file, newline='') as f:
    reader = csv.reader(f)
    models = list(reader)
    
print(len(models[0]))


19


In [6]:
model_file

'../../data/models_mov.csv'

In [7]:
df = pd.read_csv("../../data/kaggle_data/ufc-master.csv")

In [8]:
#Load the matches that have already occurred 

#df["Winner"] = df["Winner"].astype('category')
df = df[(df['Winner'] == 'Blue') | (df['Winner'] == 'Red')]

#Let's fix the date
df['date'] = pd.to_datetime(df['date'])

In [9]:
def return_finish_type(winner, finish):
    #print(winner, finish)
    #Why overcomplicate things?  We can just use a few if statements
    if winner == 'Red':
        #print("HI")
        if finish in ['U-DEC', 'S-DEC', 'M-DEC']:
            return ('Red - DEC')
        if finish in ['SUB']:
            return('Red - SUB')
        if finish in ['KO/TKO', 'DQ']:
            return('Red - KO/TKO')
    if winner == 'Blue':
        if finish in ['U-DEC', 'S-DEC', 'M-DEC']:
            return ('Blue - DEC')
        if finish in ['SUB']:
            return('Blue - SUB')
        if finish in ['KO/TKO', 'DQ']:
            return('Blue - KO/TKO')
        
    #Test for NaN
    if finish != finish:
        return('')
    
    if finish == 'Overturned':
        return('')
    
    
    return ('error')

In [10]:
len(df)

4783

In [11]:
#This calls for the power of lambda!
df['finish_type'] = df.apply(lambda x: return_finish_type(x['Winner'], x['finish']), axis=1)

In [12]:
mask = df['finish_type'] == 'error'

display(df[['Winner', 'finish', 'finish_type']][mask])

Empty DataFrame
Columns: [Winner, finish, finish_type]
Index: []

In [13]:
from sklearn import preprocessing #Used for LabelEncoder

le = preprocessing.LabelEncoder()

le.fit(df['finish_type'])

display(le.classes_)

df['label'] = le.transform(df['finish_type'])

display(df)


array(['', 'Blue - DEC', 'Blue - KO/TKO', 'Blue - SUB', 'Red - DEC',
       'Red - KO/TKO', 'Red - SUB'], dtype=object)

R_fighter         B_fighter  R_odds  B_odds        R_ev  \
0     Dustin Poirier    Conor McGregor    -129     100   77.519380   
1      Gilbert Burns  Stephen Thompson     130    -162  130.000000   
2        Tai Tuivasa        Greg Hardy    -130     105   76.923077   
3       Irene Aldana   Yana Kunitskaya    -107    -115   93.457944   
4      Sean O'Malley     Kris Moutinho   -1000     580   10.000000   
...              ...               ...     ...     ...         ...   
4778    Duane Ludwig     Darren Elkins    -155     135   64.516129   
4779     John Howard    Daniel Roberts    -210     175   47.619048   
4780  Brendan Schaub     Chase Gormley    -260     220   38.461538   
4781     Mike Pierce     Julio Paulino    -420     335   23.809524   
4782    Eric Schafer       Jason Brilz     140    -160  140.000000   

            B_ev       date                   location country Winner  ...  \
0     100.000000 2021-07-10     Las Vegas, Nevada, USA     USA    Red  ...   
1      61.728395 2021-07-10     Las Vegas, Nevada, USA     USA    Red  ...   
2     105.000000 2021-07-10     Las Vegas, Nevada, USA     USA    Red  ...   
3      86.956522 2021-07-10     Las Vegas, Nevada, USA     USA    Red  ...   
4     580.000000 2021-07-10     Las Vegas, Nevada, USA     USA    Red  ...   
...          ...        ...                        ...     ...    ...  ...   
4778  135.000000 2010-03-21  Broomfield, Colorado, USA     USA   Blue  ...   
4779  175.000000 2010-03-21  Broomfield, Colorado, USA     USA    Red  ...   
4780  220.000000 2010-03-21  Broomfield, Colorado, USA     USA    Red  ...   
4781  335.000000 2010-03-21  Broomfield, Colorado, USA     USA    Red  ...   
4782   62.500000 2010-03-21  Broomfield, Colorado, USA     USA   Blue  ...   

      R_rev_bout B_rev_bout r_dec_odds  b_dec_odds  r_sub_odds  b_sub_odds  \
0            NaN        NaN      550.0       700.0       575.0      2200.0   
1            NaN        NaN      400.0       150.0       475.0      2500.0   
2            NaN        NaN      350.0       350.0      1600.0      1800.0   
3            NaN        NaN      160.0       150.0      1200.0      1200.0   
4            NaN        NaN      400.0      1400.0       800.0      1600.0   
...          ...        ...        ...         ...         ...         ...   
4778         0.0        0.0        NaN         NaN         NaN         NaN   
4779         0.0        1.0        NaN         NaN         NaN         NaN   
4780         0.0        0.0        NaN         NaN         NaN         NaN   
4781         0.0        0.0        NaN         NaN         NaN         NaN   
4782         1.0        1.0        NaN         NaN         NaN         NaN   

      r_ko_odds  b_ko_odds    finish_type  label  
0         165.0      150.0   Red - KO/TKO      5  
1         525.0      250.0      Red - DEC      4  
2         160.0      265.0   Red - KO/TKO      5  
3         425.0      800.0   Red - KO/TKO      5  
4        -300.0     1200.0   Red - KO/TKO      5  
...         ...        ...            ...    ...  
4778        NaN        NaN  Blue - KO/TKO      2  
4779        NaN        NaN   Red - KO/TKO      5  
4780        NaN        NaN   Red - KO/TKO      5  
4781        NaN        NaN      Red - DEC      4  
4782        NaN        NaN     Blue - DEC      1  

[4783 rows x 145 columns]

In [14]:
label_df = df['label']
df_odds = df[['r_dec_odds', 'r_sub_odds', 'r_ko_odds', 'b_dec_odds', 'b_sub_odds', 'b_ko_odds']]


df_train = df[250:]
label_train = label_df[250:]
odds_train = df_odds[250:]

df_test = df[:250]
label_test = label_df[:250]
odds_test = df_odds[:250]

print(len(df_test))
print(len(label_test))
print(len(odds_test))


250
250
250


In [15]:
weightclass_list = ['B_match_weightclass_rank', 'R_match_weightclass_rank', "R_Women's Flyweight_rank", "R_Women's Featherweight_rank", "R_Women's Strawweight_rank", "R_Women's Bantamweight_rank", 'R_Heavyweight_rank', 'R_Light Heavyweight_rank', 'R_Middleweight_rank', 'R_Welterweight_rank', 'R_Lightweight_rank', 'R_Featherweight_rank', 'R_Bantamweight_rank', 'R_Flyweight_rank', 'R_Pound-for-Pound_rank', "B_Women's Flyweight_rank", "B_Women's Featherweight_rank", "B_Women's Strawweight_rank", "B_Women's Bantamweight_rank", 'B_Heavyweight_rank', 'B_Light Heavyweight_rank', 'B_Middleweight_rank', 'B_Welterweight_rank', 'B_Lightweight_rank', 'B_Featherweight_rank', 'B_Bantamweight_rank', 'B_Flyweight_rank', 'B_Pound-for-Pound_rank']
df_train[weightclass_list] = df_train[weightclass_list].fillna(17)
df_test[weightclass_list] = df_test[weightclass_list].fillna(17)

C:\Users\matth\anaconda3\lib\site-packages\pandas\core\frame.py:3191: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[k1] = value[k2]


In [16]:
#We need to split then mask.  The models can never see the first 250 rows.

mask = df_train['finish_type'] != ''
df_train = df_train[mask]
#print(len(df_train))

mask = df_test['finish_type'] != ''
df_test = df_test[mask]
#print(len(df_test))

label_train = label_train[label_train.index.isin(df_train.index)]
label_test = label_test[label_test.index.isin(df_test.index)]

odds_train = odds_train[odds_train.index.isin(df_train.index)]
odds_test = odds_test[odds_test.index.isin(df_test.index)]


print(len(df_train))
print(len(label_train))
print(len(odds_train))
print(len(df_test))
print(len(label_test))
print(len(odds_test))

4293
4293
4293
250
250
250


In [17]:
odds_train = odds_train.dropna()
odds_test = odds_test.dropna()

df_train = df_train[df_train.index.isin(odds_train.index)]
df_test = df_test[df_test.index.isin(odds_test.index)]

label_train = label_train[label_train.index.isin(odds_train.index)]
label_test = label_test[label_test.index.isin(odds_test.index)]

print(len(df_train))
print(len(label_train))
print(len(odds_train))
print(len(df_test))
print(len(label_test))
print(len(odds_test))

3255
3255
3255
239
239
239


In [18]:
model_num = 0

In [19]:
print(odds_test.columns)
print(le.classes_)

Index(['r_dec_odds', 'r_sub_odds', 'r_ko_odds', 'b_dec_odds', 'b_sub_odds',
       'b_ko_odds'],
      dtype='object')
['' 'Blue - DEC' 'Blue - KO/TKO' 'Blue - SUB' 'Red - DEC' 'Red - KO/TKO'
 'Red - SUB']


In [20]:
odds_test.rename(columns={'r_dec_odds': 'Red - DEC', 'r_sub_odds': 'Red - SUB', 'r_ko_odds': 'Red - KO/TKO',
                'b_dec_odds': 'Blue - DEC', 'b_sub_odds': 'Blue - SUB', 'b_ko_odds': 'Blue - KO/TKO'}, inplace=True)
odds_train.rename(columns={'r_dec_odds': 'Red - DEC', 'r_sub_odds': 'Red - SUB', 'r_ko_odds': 'Red - KO/TKO',
                'b_dec_odds': 'Blue - DEC', 'b_sub_odds': 'Blue - SUB', 'b_ko_odds': 'Blue - KO/TKO'}, inplace=True)


In [21]:
score_list = []

In [22]:
score_list = []
for model_num in range(len(models[0])):
    test_model_name = models[0][model_num]
    test_model = eval(models[1][model_num])
    test_model_features = eval(models[2][model_num])
    test_model_ev = eval(models[3][model_num])
    score_list.append(evaluate_model_mov(test_model, test_model_features, test_model_ev, df_train, label_train, odds_train, df_test, label_test,
                         odds_test, le.classes_, verbose = True))



(2782, 2)

(2782,)

(2782, 6)

(239, 2)

(239,)

...

114     -160.0      550.0         750.0       350.0      1400.0         1200.0
Blue - DEC: 0.11636571382401839
350.0
-47.63542877919172

Blue - KO/TKO: 0.09942654747093288
1200.0
29.254511712212746
1
Losing Bet.  New Score: -2785.0

Blue - SUB: 0.0420494048526011
1400.0
-36.92589272109835

Red - DEC: 0.42839630353106234
-160.0
-30.385600676202372

Red - KO/TKO: 0.14645579306365333
750.0
24.48742410410533
4
Losing Bet.  New Score: -2885.0

Red - SUB: 0.1673062372577316
550.0
8.749054217525554
5
Losing Bet.  New Score: -2985.0

Result: Red - DEC (4)
     Red - DEC  Red - SUB  Red - KO/TKO  Blue - DEC  Blue - SUB  Blue - KO/TKO
115      150.0      450.0         800.0       250.0       700.0          650.0
Blue - DEC: 0.1270222025670969
250.0
-55.5422291015161

Blue - KO/TKO: 0.16166613461910093
650.0
21.249600964325694
1
Losing Bet.  New Score: -3085.0

Blue - SUB: 0.06520413036278518
700.0
-47.83669570977187

Red - DEC: 0.320210040431174
150.0
-19.947489892206498

Red - KO/TKO: 0.1789686

Losing Bet.  New Score: -3820.0

Red - KO/TKO: 0.0960911215485789
650.0
-27.931658838565816

Red - SUB: 0.1243439936954035
1400.0
86.51599054310525
5
Losing Bet.  New Score: -3920.0

Result: Blue - DEC (1)
     Red - DEC  Red - SUB  Red - KO/TKO  Blue - DEC  Blue - SUB  Blue - KO/TKO
142      190.0      700.0         375.0       210.0      1000.0          500.0
Blue - DEC: 0.19201179232111154
210.0
-40.476344380455416

Blue - KO/TKO: 0.15384856031771008
500.0
-7.690863809373951

Blue - SUB: 0.05638586071092339
1000.0
-37.975553217984256

Red - DEC: 0.3283641255864179
190.0
-4.774403579938799

Red - KO/TKO: 0.18496100803686572
375.0
-12.143521182488783

Red - SUB: 0.0844286530269711
700.0
-32.45707757842312

Result: Red - KO/TKO (5)
     Red - DEC  Red - SUB  Red - KO/TKO  Blue - DEC  Blue - SUB  Blue - KO/TKO
143      375.0     1100.0         450.0       475.0       650.0          115.0
Blue - DEC: 0.280132206372413
475.0
61.076018664137464
0
Losing Bet.  New Score: -4020.0

Blue - KO/

170      200.0      600.0         500.0       180.0       800.0          600.0
Blue - DEC: 0.2483087010034408
180.0
-30.47356371903657

Blue - KO/TKO: 0.14189125737925068
600.0
-0.6761198345245276

Blue - SUB: 0.08040428453272189
800.0
-27.63614392055031

Red - DEC: 0.30284153477404063
200.0
-9.14753956778781

Red - KO/TKO: 0.1323462192906203
500.0
-20.59226842562782

Red - SUB: 0.09420800301992609
600.0
-34.054397886051746

Result: Blue - DEC (1)
     Red - DEC  Red - SUB  Red - KO/TKO  Blue - DEC  Blue - SUB  Blue - KO/TKO
171      235.0      300.0        1200.0       170.0       675.0          525.0
Blue - DEC: 0.25882200175479747
170.0
-30.118059526204675

Blue - KO/TKO: 0.13637737481369347
525.0
-14.764140741441565

Blue - SUB: 0.05811459425357028
675.0
-54.96118945348303

Red - DEC: 0.33859360327443183
235.0
13.428857096934664
3
4 4
Winning Bet. New Score: -6485.0

Red - KO/TKO: 0.0935895603509183
1200.0
21.666428456193785
4
Losing Bet.  New Score: -6585.0

Red - SUB: 0.114502865

1200.0
-21.588131161536964

Red - DEC: 0.3597883638453452
300.0
43.91534553813807
3
Losing Bet.  New Score: -5600.0

Red - KO/TKO: 0.11915829720957995
375.0
-43.39980882544953

Red - SUB: 0.1453844150938061
800.0
30.84597358442548
5
Losing Bet.  New Score: -5700.0

Result: Blue - DEC (1)
     Red - DEC  Red - SUB  Red - KO/TKO  Blue - DEC  Blue - SUB  Blue - KO/TKO
198      105.0      900.0         375.0       250.0      1200.0          700.0
Blue - DEC: 0.17165680747403153
250.0
-39.92011738408896

Blue - KO/TKO: 0.14223053437424538
700.0
13.784427499396301
1
Losing Bet.  New Score: -5800.0

Blue - SUB: 0.052092056589037684
1200.0
-32.28032643425101

Red - DEC: 0.3300951205951246
105.0
-32.33050027799946

Red - KO/TKO: 0.2135889047585856
375.0
1.4547297603281635
4
Losing Bet.  New Score: -5900.0

Red - SUB: 0.09033657620897526
900.0
-9.66342379102474

Result: Red - DEC (4)
     Red - DEC  Red - SUB  Red - KO/TKO  Blue - DEC  Blue - SUB  Blue - KO/TKO
199     -125.0      600.0         

225      600.0     2500.0         115.0       550.0       175.0          800.0
Blue - DEC: 0.2048497218189658
550.0
33.15231918232777
0
Losing Bet.  New Score: -8075.0

Blue - KO/TKO: 0.25144663528071615
800.0
126.30197175264452
1
Losing Bet.  New Score: -8175.0

Blue - SUB: 0.06336135738967869
175.0
-82.57562671783836

Red - DEC: 0.14788500543680955
600.0
3.519503805766675
3
Losing Bet.  New Score: -8275.0

Red - KO/TKO: 0.2697850887916818
115.0
-41.99620590978842

Red - SUB: 0.06267219128214825
2500.0
62.94769733358547
5
Losing Bet.  New Score: -8375.0

Result: Red - KO/TKO (5)
     Red - DEC  Red - SUB  Red - KO/TKO  Blue - DEC  Blue - SUB  Blue - KO/TKO
226      400.0      900.0        2000.0      -135.0       850.0          300.0
Blue - DEC: 0.2974642944015695
-135.0
-48.21917838194901

Blue - KO/TKO: 0.13907158793774313
300.0
-44.37136482490275

Blue - SUB: 0.07162967397465816
850.0
-31.951809724074742

Red - DEC: 0.27264095756074136
400.0
36.32047878037068
3
Losing Bet.  New Sco

In [23]:
models[4] = score_list

In [24]:
with open(model_file, 'w' , newline='') as outfile:
    writer = csv.writer(outfile)
    for row in models:
        #print("HI")
        writer.writerow(row)
    
outfile.close()

In [25]:
print(score_list)

[-10545.0, -16475.0, -11317.0, -2783.5911885327178, -14.74512396926184, -5840.0, -4785.0, -5188.404853128991, -9624.210144927536, -5235.0, -9742.0, -24625.0, -7284.444444444444, -6412.0, -3570.0, -7655.0, -8440.0, -11055.0, -7950.0]


In [26]:
models[4] = score_list

In [27]:
print(score_list)

[-10545.0, -16475.0, -11317.0, -2783.5911885327178, -14.74512396926184, -5840.0, -4785.0, -5188.404853128991, -9624.210144927536, -5235.0, -9742.0, -24625.0, -7284.444444444444, -6412.0, -3570.0, -7655.0, -8440.0, -11055.0, -7950.0]
